In [2]:
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
from torchvision import datasets
from transformers import AutoTokenizer, AutoModel
import pandas as pd
import torch
import torch.nn as nn
import torch.optim as optim
import math

In [92]:
tokenizer = AutoTokenizer.from_pretrained("SZTAKI-HLT/hubert-base-cc")
model = AutoModel.from_pretrained("SZTAKI-HLT/hubert-base-cc")

Data

The structure we expect is a 2x2x768 dim output

I used the other notebook, so i can have my functions, i'll implement them here too, if needed

Def functions

In [93]:
#it wants the sentences as a list already split to words/punctuation
#in the first column
def text_tokenizing(text_dataframe, the_tokenizer):
    input_ids=[]
    attention_masks=[]
    targets=[]
    for_preparing=the_tokenizer("")
    start_symbol=for_preparing.input_ids[0]
    end_symbol=for_preparing.input_ids[-1]
    
    for i in range(text_dataframe["sentence"].size):
        target_idx_counter=text_dataframe["target_idx"][i]
        input_ids_sentence=[]
        attention_masks_sentence=[]
        input_ids_sentence.append(start_symbol)
        attention_masks_sentence.append(1)
        
        for j in range(len(text_dataframe["sentence"][i])):
            
            #a word is text_daraframe.iloc[i,0][j]
            tokenized_word=the_tokenizer(
                                     text_dataframe["sentence"][i][j],
                                     add_special_tokens=False
                                    )
            
            input_id=tokenized_word.input_ids
            attention_mask=tokenized_word.attention_mask
                
            if(text_dataframe["sentence"][i][j]==text_dataframe["word"][i]):
                target=len(input_id)
                text_dataframe["target_idx"][i]=len(input_ids_sentence)           
            
            input_ids_sentence.extend(input_id)
            attention_masks_sentence.extend(attention_mask)
        
        input_ids_sentence.append(end_symbol)
        attention_masks_sentence.append(1)
        input_ids.append(input_ids_sentence)
        attention_masks.append(attention_masks_sentence)
        targets.append(target)
        
    #padding    
    max_length_ids=longest_sentence_size(input_ids)
    
    for i in range(len(input_ids)):
        current_size=len(input_ids[i])
        additional_zeros=[]
        for j in range(max_length_ids-current_size):
            additional_zeros.append(0)
        
        input_ids[i]=input_ids[i][0:-1]+additional_zeros+[input_ids[i][-1]]
        attention_masks[i]=attention_masks[i][0:-1]+additional_zeros+[attention_masks[i][-1]]


        
    tokenized_text=pd.DataFrame({
        'sentence': text_dataframe["sentence"],
        'word': text_dataframe["word"],
        'target_idx': text_dataframe["target_idx"],
        'target_length': targets,
        'type': text_dataframe["type"],
        'input_id': input_ids,
        'attention_mask': attention_masks
    })
    return tokenized_text

In [94]:
#we add 2 more to it, because we will use it to measure the sentences for
#the tokenizer, which has a starting and an end character additionally

def longest_sentence_size(sentences):
    current_max=0
    for sentence in sentences:
        if(len(sentence)>current_max):
            current_max=len(sentence)
    return current_max+2

Take datas out of files to pandas DataFrames

TODO: change it to a function

In [95]:
train_path="conf/data/number_noun/train.tsv"
train_data = pd.read_csv(
    train_path,
    sep='\t',
    names=['sentence',
           'word',
           'target_idx',
           'type'
          ],
    quoting=3
)
print(train_data)
print(train_data["sentence"][245], train_data["sentence"][246], train_data["sentence"][247], train_data["sentence"][245])
train_sentences = train_data.sentence.str.split(" ").to_frame()

train_data["sentence"]=train_sentences
train_data

                                               sentence                  word  \
0     A tulajdonviszonyok – s talán a hatalom – igaz...     tulajdonviszonyok   
1     Szintén pofátlan sztereotípia " magyar társada...           fordulatait   
2     Eljárásrend a TÁMOP-3.3.8-2/12-2012-0092 számú...           Eljárásrend   
3     Ezért honlapunk jelentősen eltér a kulturális ...           portáloktól   
4     Ugyanakkor a terület állapotának romlása azzal...       következménnyel   
...                                                 ...                   ...   
1995  Az SAP Business One segítségével valamennyi te...        folyamatainkat   
1996  Feltűnően sok volt a kutya és nem akármilyenek...               fajtáik   
1997  A kocsiszekrény borítólemezein kisebb-nagyobb ...        borítólemezein   
1998  Az ösztöndíjpályázattal kapcsolatos központi a...  ösztöndíjpályázattal   
1999  A fenti együttműködési kötelezettség megszegés...             bírságtól   

      target_idx  type  
0 

sentence                  word  \
0     [A, tulajdonviszonyok, –, s, talán, a, hatalom...     tulajdonviszonyok   
1     [Szintén, pofátlan, sztereotípia, ", magyar, t...           fordulatait   
2     [Eljárásrend, a, TÁMOP-3.3.8-2/12-2012-0092, s...           Eljárásrend   
3     [Ezért, honlapunk, jelentősen, eltér, a, kultu...           portáloktól   
4     [Ugyanakkor, a, terület, állapotának, romlása,...       következménnyel   
...                                                 ...                   ...   
1995  [Az, SAP, Business, One, segítségével, valamen...        folyamatainkat   
1996  [Feltűnően, sok, volt, a, kutya, és, nem, akár...               fajtáik   
1997  [A, kocsiszekrény, borítólemezein, kisebb-nagy...        borítólemezein   
1998  [Az, ösztöndíjpályázattal, kapcsolatos, közpon...  ösztöndíjpályázattal   
1999  [A, fenti, együttműködési, kötelezettség, megs...             bírságtól   

      target_idx  type  
0              1  Plur  
1             17  Plur  
2              0  Sing  
3              7  Plur  
4              7  Sing  
...          ...   ...  
1995          10  Plur  
1996          11  Plur  
1997           2  Plur  
1998           1  Sing  
1999          26  Sing  

[2000 rows x 4 columns]

In [96]:
dev_data = pd.read_csv(
    "conf/data/number_noun/dev.tsv",
    sep='\t',
    names=['sentence',
           'word',
           'target_idx',
           'type'
          ]
)
dev_sentences = dev_data.sentence.str.split(" ").to_frame()
dev_data["sentence"] = dev_sentences
dev_data

ParserError: Error tokenizing data. C error: EOF inside string starting at row 79

In [ ]:
dev_data

In [50]:
train_data.columns

Index(['sentence', 'word', 'target_idx', 'type'], dtype='object')

In [22]:
len(tokenized_dev_data["attention_mask"][0])

77

In [23]:
test_length=torch.LongTensor([tokenized_dev_data["input_id"],
                tokenized_dev_data["attention_mask"]])
test_length[0][5]

tensor([    2, 16039, 15257,  2005,  2446, 16927,  3576,  2079,  2005, 13795,
        21575, 26317,  9012,  3483,  7776,  2267,  2005, 22362,  2178,  3866,
         2029,  2227, 18088, 31441, 25699,  3446,  3576,  2005,  2876, 10958,
         2040,  2218,  8368,  2075,  2033,  5200,  9448,  2235, 29914,  2098,
         3425,  2005, 23503,  2416, 13269, 31742,  8647,  2607, 26952,  3254,
         2081,  3923,  5361,  2332,  4575,     0,     0,     0,     0,     0,
            0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
            0,     0,     0,     0,     0,     0,     3])

In [135]:
#WRONG
#
#
#
tokenized_dev_data=text_tokenizing(dev_data)
with torch.no_grad():
    test = tokenized_dev_data.apply(lambda x: model(
            torch.LongTensor([tokenized_dev_data["input_id"],
                tokenized_dev_data["attention_mask"]]),
            output_hidden_states=True
        ), axis=0)
test

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


sentence          [Emellett, cél, olyan, nagy, tömegközlekedési,...
word                                                            cél
target_idx                                                        3
target_length                                                     2
type                                                           Sing
input_id          [101, 11289, 76506, 171, 24817, 22361, 17221, ...
attention_mask    [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...
dtype: object

Let Data through the Model, and tokenize it

In [57]:
list=[1,2,3,4,5]
for lili in list[0:7]:
    print(lili)

1
2
3
4
5


In [8]:
class BatchIterator_model:
    def __init__(self, id, ma, ti, tl, batch_size):
        self.id = id
        self.ma = ma
        self.ti = ti
        self.tl = tl
        self.batch_size = batch_size
        
    def iterate_once(self):
        for start in range(0, len(self.id), self.batch_size):
            end = start + self.batch_size
            if(end > len(self.id)):
                end= len(self.id)
            yield   self.id[start:end], self.ma[start:end], self.ti[start:end], self.tl[start:end]

HERE

HEY

HERE

!!!!!

In [97]:
tokenized_dev_data=text_tokenizing(dev_data, tokenizer)

tokenized_train_data=text_tokenizing(train_data, tokenizer)

train_batch_size = math.ceil(tokenized_train_data["input_id"].size/50)
dev_batch_size = math.ceil(tokenized_dev_data["input_id"].size/5)

dev_outputs=pd.DataFrame({})

model_dev_iterator = BatchIterator_model(
                        torch.tensor(tokenized_dev_data["input_id"]),
                        torch.tensor(tokenized_dev_data["attention_mask"]),
                        torch.tensor(tokenized_dev_data["target_idx"]),
                        torch.tensor(tokenized_dev_data["target_length"]),
                        dev_batch_size
                        )

#for testing_this in tokenized_dev_data.groupby(np.arange(len(tokenized_dev_data["input_id"]))//5):
#    print(testing_this)
    

for batch_id, batch_ma, batch_ti, batch_tl in model_dev_iterator.iterate_once():

    batch_id_tensor=torch.LongTensor(batch_id)
    batch_ma_tensor=torch.LongTensor(batch_ma)

    with torch.no_grad():
        output=model(
            input_ids=batch_id_tensor,
            attention_mask=batch_ma_tensor,
            output_hidden_states=True,
            return_dict=True
        )
    
    for i in range(len(batch_id_tensor)):

        target_index = (batch_ti[i] + batch_tl[i] - 1)
        #dev_outputs.append(output[2][0][i][target_index])     
        dev_outputs.insert(len(dev_outputs.columns), len(dev_outputs.columns)-1, output[2][0][i][target_index], True)


print(dev_outputs)

train_outputs=pd.DataFrame({})

model_train_iterator = BatchIterator_model(
                        torch.tensor(tokenized_train_data["input_id"]),
                        torch.tensor(tokenized_train_data["attention_mask"]),
                        torch.tensor(tokenized_train_data["target_idx"]),
                        torch.tensor(tokenized_train_data["target_length"]),
                        train_batch_size
                        )
    

for batch_id, batch_ma, batch_ti, batch_tl in model_train_iterator.iterate_once():

    batch_id_tensor=torch.LongTensor(batch_id)
    batch_ma_tensor=torch.LongTensor(batch_ma)

    with torch.no_grad():
        output=model(
            input_ids=batch_id_tensor,
            attention_mask=batch_ma_tensor,
            output_hidden_states=True,
            return_dict=True
        )
    print(output)
    for i in range(len(batch_id_tensor)):

        target_index = (batch_ti[i] + batch_tl[i] - 1)
        train_outputs.insert(len(train_outputs.columns), len(train_outputs.columns)-1, output[2][0][i][target_index], True)   



C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


         -1         0         1         2         3         4         5    \
0    1.043752 -0.028789 -0.097321  0.204860  0.704241 -0.031874  0.097440   
1   -0.326490  0.393201 -0.030249  0.769604  0.659024  0.582586 -0.809946   
2   -1.321445  0.163464 -0.737761  0.728142 -0.112068  0.065921  0.167486   
3    0.000036 -0.162014 -0.509131 -0.743331 -0.032409  0.578664 -0.861923   
4   -0.896512 -0.758857 -0.159870 -0.837757 -0.225451 -0.192912 -2.412647   
..        ...       ...       ...       ...       ...       ...       ...   
763 -0.034325 -0.544449  0.250085 -0.334385 -0.140649 -0.037566  1.306185   
764 -1.287570  0.044658  0.139993  0.879447  0.194832 -0.298384 -0.482188   
765 -0.096112  0.277310 -0.278612 -0.440368  0.210697 -0.839808 -1.241264   
766 -1.108201 -0.684364 -1.652619 -0.301671  1.017691  1.094016 -0.220901   
767  0.471358 -0.194171 -0.474897 -0.481238 -0.114592 -0.102356 -0.881584   

          6         7         8    ...       188       189       190  \
0  

BaseModelOutputWithPooling(last_hidden_state=tensor([[[ 5.7135e-01, -5.7894e-01, -9.1085e-01,  ..., -3.4671e-02,
          -1.1039e+00,  8.9234e-02],
         [-3.3174e-01, -3.0275e-01, -7.9534e-01,  ..., -1.8647e-01,
          -3.4505e-01,  8.7471e-02],
         [-2.2709e-01, -1.0647e+00, -1.3652e+00,  ..., -1.8389e-01,
           1.9358e-01, -2.7595e-02],
         ...,
         [-3.7175e-01, -4.6274e-01, -5.6146e-02,  ...,  3.9376e-01,
          -2.5835e-01,  4.8980e-01],
         [ 3.0755e-02, -6.1621e-01,  5.5688e-03,  ...,  3.2792e-01,
          -5.0830e-01,  4.8005e-01],
         [-4.0932e-02,  5.6019e-02,  9.4805e-02,  ...,  2.2419e-02,
          -1.0311e-01,  3.1281e-01]],

        [[ 8.8424e-01, -1.5969e-01,  5.4592e-01,  ...,  4.6639e-01,
           1.3868e-01, -4.3385e-01],
         [ 2.8354e-01, -2.6822e-01,  4.7498e-02,  ..., -3.9455e-02,
           5.6539e-01,  1.6740e-01],
         [ 6.7065e-01,  4.6272e-01,  6.3111e-01,  ..., -3.9185e-01,
           1.8660e-01,  7.4878e

BaseModelOutputWithPooling(last_hidden_state=tensor([[[ 0.4418,  0.2849,  0.6919,  ...,  0.4720, -0.9042, -0.1747],
         [-0.7491, -0.0160, -0.2436,  ..., -0.0635, -0.3091, -0.1080],
         [-0.3967,  0.2947, -0.3978,  ..., -0.1014, -0.0451,  0.1502],
         ...,
         [-0.2029, -0.2242,  0.7036,  ...,  0.0272, -0.1440,  0.0452],
         [-0.2211, -0.1785,  0.6999,  ...,  0.0263, -0.1554,  0.0677],
         [ 0.0393,  0.0770,  0.2214,  ...,  0.0936, -0.0444,  0.1132]],

        [[ 1.0235, -0.2211, -0.4636,  ..., -0.0840,  0.1382, -0.0499],
         [-0.2463,  0.1040, -0.4629,  ..., -0.5283,  0.2302,  0.6003],
         [ 0.5205,  0.0062, -0.9496,  ..., -0.4392,  0.4818,  0.7514],
         ...,
         [ 0.1772, -0.3115,  0.1514,  ...,  0.1292,  0.0522,  0.2857],
         [-0.0405, -0.2201,  0.1406,  ...,  0.2853, -0.0480,  0.1644],
         [ 0.1090,  0.0660,  0.0460,  ..., -0.0235,  0.0697,  0.2567]],

        [[ 0.9209, -0.1182, -0.1848,  ...,  0.1184,  0.0903, -0.4617],


BaseModelOutputWithPooling(last_hidden_state=tensor([[[ 0.8765, -0.1142, -0.0869,  ...,  0.0371,  0.1586, -0.4802],
         [-0.0154, -0.0241, -0.1989,  ...,  0.0265,  0.1978,  0.0633],
         [-0.1814, -0.3084,  0.2823,  ..., -0.7611,  0.3251, -0.3214],
         ...,
         [-0.0515, -0.2900,  0.2854,  ...,  0.2494,  0.5415, -0.1056],
         [-0.4034, -0.2745,  0.2693,  ...,  0.2123,  0.2447, -0.0103],
         [ 0.1113, -0.0250,  0.0953,  ...,  0.0211,  0.0608,  0.0901]],

        [[ 0.3955,  0.7374, -0.4593,  ...,  0.2289,  0.5296, -0.3247],
         [ 0.3309,  0.4159, -0.3215,  ...,  0.0026,  0.2364,  0.2438],
         [ 0.0489,  0.5206, -1.0864,  ...,  0.1312, -0.1013, -0.0804],
         ...,
         [ 0.2789, -0.5189,  0.2841,  ...,  0.5741,  0.2775,  0.1187],
         [ 0.0333, -0.5072,  0.2645,  ...,  0.5036,  0.3433,  0.0828],
         [ 0.0731,  0.1681,  0.0399,  ..., -0.0653,  0.0520,  0.1394]],

        [[ 1.0211, -0.3853,  0.5791,  ...,  0.0425,  0.0652,  0.3754],


...

BaseModelOutputWithPooling(last_hidden_state=tensor([[[-0.0517,  0.3184,  0.1410,  ...,  0.3584,  0.3023,  0.7300],
         [-0.3254,  0.4022,  0.2577,  ...,  0.0477,  0.8293,  0.6217],
         [-0.2075,  0.3954,  0.2341,  ...,  0.3686,  0.7217,  0.4586],
         ...,
         [ 0.3068, -0.3801,  0.3796,  ...,  0.6297,  0.0335,  0.4983],
         [-0.0135, -0.3895,  0.3481,  ...,  0.5333,  0.1022,  0.2677],
         [-0.0453,  0.1362,  0.0524,  ...,  0.0809,  0.0866,  0.4055]],

        [[ 0.2931, -0.7409,  0.5478,  ..., -0.7768,  0.0238, -0.2936],
         [-0.0110, -0.1120, -0.4535,  ..., -0.5230,  0.0864,  0.1470],
         [ 0.7025, -0.2579,  0.2441,  ..., -0.5841,  0.4357,  0.2901],
         ...,
         [-0.4942, -0.5761,  0.6860,  ..., -0.2533,  0.0179,  0.0372],
         [-0.1593, -0.6416,  0.6562,  ..., -0.2498,  0.0563, -0.0228],
         [ 0.0804, -0.1323,  0.1883,  ..., -0.0819,  0.0301,  0.1641]],

        [[ 0.7438, -0.2561,  0.6925,  ...,  0.5227, -0.2719, -0.3219],


BaseModelOutputWithPooling(last_hidden_state=tensor([[[ 1.1960e+00, -5.1821e-01,  9.3819e-01,  ..., -6.9272e-01,
          -5.6384e-01,  1.2354e-01],
         [ 9.8585e-02, -2.8242e-01, -3.2662e-01,  ..., -6.0778e-01,
          -3.1968e-01, -8.5435e-02],
         [ 6.4828e-01, -1.7183e-01,  5.3753e-03,  ..., -8.1954e-01,
           1.3529e-01,  1.5630e-01],
         ...,
         [ 5.2263e-01, -8.7321e-01,  6.2292e-01,  ..., -2.5175e-02,
          -1.3648e-01,  1.9773e-01],
         [ 8.8737e-02, -5.1508e-01,  5.2160e-01,  ..., -3.5123e-01,
          -1.0857e-01,  1.8293e-01],
         [ 1.0668e-01, -5.5803e-02,  2.3064e-01,  ...,  4.5363e-02,
          -4.5505e-02,  1.7455e-01]],

        [[ 1.5446e-01, -6.7568e-01,  8.6119e-01,  ...,  4.0246e-01,
           2.8413e-01, -3.7338e-01],
         [-3.3360e-03,  1.6753e-02, -1.0582e-02,  ...,  3.5033e-01,
           3.9606e-01,  1.6777e-01],
         [ 7.0211e-02, -1.0391e-01, -3.0713e-01,  ..., -3.9177e-01,
           4.0188e-01,  2.8853e

BaseModelOutputWithPooling(last_hidden_state=tensor([[[ 1.4531e-01,  4.0038e-01, -6.8295e-01,  ..., -5.1749e-01,
          -1.0037e-01,  3.4058e-02],
         [ 6.8317e-01,  3.8680e-01, -2.3321e-01,  ..., -8.6300e-01,
           1.7866e-02, -2.1586e-01],
         [ 4.5035e-02,  5.8818e-01, -1.5529e+00,  ..., -7.2091e-01,
           7.8520e-01,  3.2736e-01],
         ...,
         [-3.0901e-01,  1.6468e-01, -2.4169e-01,  ..., -2.0272e-02,
           3.7538e-01,  2.7364e-01],
         [ 3.3386e-01,  1.3181e-01, -4.1508e-01,  ...,  1.8723e-01,
           4.7389e-01,  3.0384e-01],
         [ 1.3636e-01,  1.0033e-01,  2.5382e-02,  ..., -7.2143e-02,
           4.8964e-02,  1.5741e-01]],

        [[ 1.2649e+00, -4.9242e-01, -5.4628e-01,  ..., -2.2043e-01,
          -2.9389e-02,  4.8075e-02],
         [ 3.3342e-01, -4.9868e-01, -1.6138e-01,  ..., -7.1440e-01,
          -5.6397e-01,  2.8131e-01],
         [-3.5075e-01,  1.8986e-01, -1.2337e-01,  ..., -6.9608e-01,
          -4.8049e-01,  4.8286e

BaseModelOutputWithPooling(last_hidden_state=tensor([[[ 9.9333e-01,  1.4208e-01,  4.4812e-01,  ...,  3.6403e-01,
          -5.8161e-01, -3.0408e-01],
         [ 4.2901e-01,  2.7182e-01,  2.1218e-01,  ...,  8.6152e-02,
          -3.2526e-01,  5.7132e-01],
         [ 1.4078e-02,  6.6877e-01, -2.6967e-01,  ..., -5.5645e-01,
          -1.6613e-01,  7.1674e-01],
         ...,
         [ 3.3318e-01, -3.9725e-01,  5.4937e-01,  ...,  1.8529e-01,
          -5.6793e-02,  2.9386e-01],
         [ 3.8198e-01, -4.3090e-01,  5.6298e-01,  ...,  1.8295e-01,
          -6.3778e-02,  2.6228e-01],
         [ 1.5578e-01,  7.3278e-02,  1.8578e-01,  ...,  1.3412e-01,
          -4.9581e-02,  3.5185e-01]],

        [[ 8.1958e-01,  9.8979e-02, -8.0280e-02,  ...,  1.7118e-01,
           1.0413e-01, -2.3814e-01],
         [ 4.0765e-01,  7.6038e-02, -3.9644e-01,  ..., -3.5027e-01,
           1.6185e-01,  1.7993e-01],
         [ 4.0557e-01, -3.4977e-01, -8.9285e-01,  ..., -8.5566e-01,
          -1.7583e-01, -5.6196e

BaseModelOutputWithPooling(last_hidden_state=tensor([[[ 6.9499e-01,  4.4055e-02,  8.5864e-01,  ..., -1.8914e-01,
          -1.7513e-01, -5.7758e-01],
         [ 2.6801e-01, -1.8834e-01, -6.6102e-02,  ..., -2.5101e-01,
          -4.7316e-04,  1.3915e-01],
         [-2.0248e-02,  4.4966e-02, -5.4614e-01,  ..., -4.6768e-01,
           9.0277e-02,  1.7539e-01],
         ...,
         [ 5.9219e-01, -7.6568e-01,  7.1970e-01,  ...,  2.1037e-02,
          -2.9733e-02,  2.6724e-03],
         [ 7.3772e-02, -5.5712e-01,  5.8314e-01,  ...,  3.2332e-02,
          -8.2171e-02,  5.7641e-03],
         [ 1.5338e-02,  3.4573e-02,  2.8643e-01,  ...,  3.9119e-03,
           4.7035e-02,  1.3423e-01]],

        [[-1.0428e-01,  4.3787e-02, -2.0100e-01,  ...,  4.7750e-01,
          -3.2566e-01,  3.6784e-01],
         [ 1.3260e-01, -3.7446e-02, -7.8227e-01,  ...,  3.1688e-01,
          -3.5861e-01, -4.9252e-02],
         [-1.3433e-02, -1.5671e-01,  9.1987e-02,  ..., -4.6647e-01,
          -2.2011e-01,  4.8243e

In [20]:
flat_train_x=[]

for sentence in train_outputs:
    for word in sentence:
        flat_train_x.append(word)
        
flat_dev_x=[]

for sentence in dev_outputs:
    for word in sentence:
        flat_dev_x.append(word)

In [67]:
dev_x = torch.tensor(dev_outputs.values)
train_x = torch.tensor(train_outputs.values)

In [65]:
dev_x.size()

torch.Size([768, 199])

In [45]:
#
#
#
#

print(dev_data)
tokenized_dev_data=text_tokenizing(dev_data, tokenizer)
print(tokenized_dev_data)
print(dev_data)

dev_outputs=[]

#every sentence gets turned into tensor
#so we can let it through the mode, then save the output
for i in range(tokenized_dev_data['input_id'].size):
    
    sentence=[tokenized_dev_data["input_id"][i],
              tokenized_dev_data["attention_mask"][i]]
    
    tensor_sentence=torch.LongTensor(sentence)
    
    with torch.no_grad():
        output=model(
            tensor_sentence,
            output_hidden_states=True
        )
        
    dev_outputs.append(output)

                                              sentence            word  \
0    [Komoly, fegyvertény, például, ,, hogy, a, ház...     fegyvertény   
1    [Világosi, Gábor, szerint, a, megfigyelési, üg...        tényeket   
2    [A, olaj, világpiaci, árának, drasztikus, emel...     alakulására   
3    [Emellett, cél, olyan, nagy, tömegközlekedési,...             cél   
4    [A, Pedagógus, Szakszervezet, titkára, úgy, vé...  önkormányzatok   
..                                                 ...             ...   
194  [Eszerint, szükséges, lenne, ezek, törvényi, s...         esetben   
195  [Szerb, vádak, szerint, a, nemzetközi, közössé...       helyzetet   
196  [Véleménye, szerint, a, tervezett, új, jogszab...      forrásokat   
197  [A, múlt, keddi, kormányülést, követően, Járai...       számairól   
198  [A, tanárok, fizetésének, pedig, ismét, el, ke...    későbbiekben   

     target_idx  type  
0             2  Sing  
1            31  Plur  
2            21  Sing  
3             2

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


                                              sentence            word  \
0    [Komoly, fegyvertény, például, ,, hogy, a, ház...     fegyvertény   
1    [Világosi, Gábor, szerint, a, megfigyelési, üg...        tényeket   
2    [A, olaj, világpiaci, árának, drasztikus, emel...     alakulására   
3    [Emellett, cél, olyan, nagy, tömegközlekedési,...             cél   
4    [A, Pedagógus, Szakszervezet, titkára, úgy, vé...  önkormányzatok   
..                                                 ...             ...   
194  [Eszerint, szükséges, lenne, ezek, törvényi, s...         esetben   
195  [Szerb, vádak, szerint, a, nemzetközi, közössé...       helyzetet   
196  [Véleménye, szerint, a, tervezett, új, jogszab...      forrásokat   
197  [A, múlt, keddi, kormányülést, követően, Járai...       számairól   
198  [A, tanárok, fizetésének, pedig, ismét, el, ke...    későbbiekben   

     target_idx  target_length  type  \
0             2              2  Sing   
1            31              1 

In [9]:
train_data

sentence              word  \
0     [A, 16., század, eleje, nemcsak, az, itáliai, ...  legdicsôségesebb   
1     [Az, IndustryStock, termék, és, szolgáltatás, ...           Markoló   
2     [A, munkahelyeden, nagy, valószínűséggel, mind...      legalábbvaló   
3     [Ha, egy, igazi, gurmet, vagy, ,, akkor, is, g...        ízletesebb   
4     [Kissé, sósabb, ,, és, roppanósabb, formában, ...       roppanósabb   
...                                                 ...               ...   
1996  [Ebben, az, időben, itt, tevékenykedtek, a, ma...     legnagyobbjai   
1997  [Azután, mi, is, megjelentünk, a, KFKI-ban, ,,...            késôbb   
1998  [Előbb-utóbb, mindenkinek, kifejlődik, -jobb, ...         -rosszabb   
1999  [Akkor, lesz, a, legfinomabb, ,, legkrémesebb,...      legkrémesebb   
2000  [99., De, éltinél, is, drágábbat, veszit, ,, S...         drágábbat   

      target_idx type  
0             13  Sup  
1             13  Pos  
2             24  Sup  
3             23  Cmp  
4              4  Cmp  
...          ...  ...  
1996           8  Sup  
1997           7  Cmp  
1998          10  Cmp  
1999           5  Sup  
2000           4  Cmp  

[2001 rows x 4 columns]

In [10]:
print(len(train_data.iloc[0,0]))
print(len(train_data.iloc[1,0]))

16
16


In [ ]:
print(train_data)
tokenized_train_data=text_tokenizing(train_data)


train_outputs=[]

#every sentence gets turned into tensor
#so we can let it through the mode, then save the output
for i in range(tokenized_train_data['input_id'].size):
    
    sentence=[tokenized_train_data["input_id"][i],
              tokenized_train_data["attention_mask"][i]]
    
    tensor_sentence=torch.LongTensor(sentence)
    print(tensor_sentence)
    with torch.no_grad():
        output=model(
            tensor_sentence,
            output_hidden_states=True,
        )
        
    train_outputs.append(output)

train_outputs

                                               sentence         word  \
0     [A, szobát, ,, ahol, a, 66, éves, Kobajasi, Si...       szobát   
1     [Valami, tudat, alatt, mindig, működött, benne...     megérzés   
2     [A, megyében, a, legnagyobb, problémát, az, át...     megyében   
3     [A, tíz, kis, ,, zömében, szabolcsi, konzervgy...    hiteleire   
4     [A, 72, tagú, konferencia, által, ,, három, pü...       püspök   
...                                                 ...          ...   
1995  [Ez, a, műfaj, lényege, :, olyan, szuggesztivi...     operákat   
1996  [Egyre, nagyobb, ugyanis, a, túlélők, hatóságo...  miniszterek   
1997  [", Ki, ez, ?, ", —, kérdezte, a, magyar, komm...  kommunisták   
1998  [Az, állami, televíziófelügyelet, például, átm...    némaságra   
1999                             [Ugatják, a, telet, .]        telet   

      target_idx  type  
0              1  Sing  
1              8  Sing  
2              1  Sing  
3             33  Plur  
4         

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


tensor([[    2,  2038, 23062,  3576,  2897,  2005, 18334,  3140, 14155, 18912,
          8017, 15325,  2096,  4364, 27705, 31734,  2214,  3576,  2005, 19354,
         31735,  2478, 27517,  4391,  4332,  4575,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     3],
        [    1,     1,     1,     1,     1,     1,     1,     1,     1,     1,
             1,     1,     1,     1,     1,     1,     1,     1,     1,     1,
             1,     1,     1,     1,     1,     1,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0, 

tensor([[    2,  4037,  8318,  2066,  9405, 18003,  2986,  2033,  6248, 31795,
          4575,  4330,  3247,  2210,  2099,  7864,  3917,  2210,  5064, 18633,
         13877,  3746,  2144,  3576, 13796,  2039,  5408,  2598, 19030,  4939,
         27945,  3043,  4575,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     3],
        [    1,     1,     1,     1,     1,     1,     1,     1,     1,     1,
             1,     1,     1,     1,     1,     1,     1,     1,     1,     1,
             1,     1,     1,     1,     1,     1,     1,     1,     1,     1,
             1,     1,     1,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0, 

tensor([[    2, 16172, 31761,  6121,  9045,  2005,  4676, 26028,  3576,  2747,
          2005, 17532,  8094,  3576,  2033, 31416,  2019, 20989,  4575,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     3],
        [    1,     1,     1,     1,     1,     1,     1,     1,     1,     1,
             1,     1,     1,     1,     1,     1,     1,     1,     1,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0, 

...

             0,     0,     0,     0,     0,     0,     0,     0,     1]])
tensor([[    2, 25141,  3856,  8602,  2005, 15244,  3576,  2079,  7807, 22454,
          8253,  9466,  5291,  2066,  2509,  4058,  3576,  2641,  4600, 23430,
         10577, 17166,  3119, 31738,  2082,  2120, 14726,  2033,  6391, 12470,
         31739, 31750, 31759,  9731,  2008,  4575,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     3],
        [    1,     1,     1,     1,     1,     1,     1,     1,     1,     1,
             1,     1,     1,     1,     1,     1,     1,     1,     1,     1,
             1,     1,     1,     1,     1,     1,     1,     1,     1,     1,
             1,     1,     1,     1,     1,     1,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0

tensor([[    2, 21510,  2911,  2005,  9965,  3894,  2349,  2816, 25625,  2925,
          4575,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     3],
        [    1,     1,     1,     1,     1,     1,     1,     1,     1,     1,
             1,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0, 

tensor([[    2,  2038,  3174,  9202,  2127,  2233,  2005, 23676, 31742,  2343,
         29805,  4575,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     3],
        [    1,     1,     1,     1,     1,     1,     1,     1,     1,     1,
             1,     1,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0, 

tensor([[    2, 16039,  2972,  2146,  4318,  2033,  6325, 14981,  3576,  2005,
         22374,  6683,  3576, 21065,  6683,  5502, 24935,  4575,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     3],
        [    1,     1,     1,     1,     1,     1,     1,     1,     1,     1,
             1,     1,     1,     1,     1,     1,     1,     1,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0, 

tensor([[    2,  2566,  2233,  2489,  7161,  3576,  2045,  2093,  2523,  2122,
          3576,  3612,  6746, 18431,  3013,  2005,  5022, 28117,  2332,  2060,
         31765, 23950,  6665,  2143, 27249,  3576,  2079, 21296, 31742, 17389,
          2072, 15826,  4575,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     3],
        [    1,     1,     1,     1,     1,     1,     1,     1,     1,     1,
             1,     1,     1,     1,     1,     1,     1,     1,     1,     1,
             1,     1,     1,     1,     1,     1,     1,     1,     1,     1,
             1,     1,     1,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0, 

In [12]:
print(len(tokenized_train_data["attention_mask"][0]))
print(len(tokenized_train_data["attention_mask"][1]))

99
99


In [13]:
len(tokenized_dev_data["input_id"][0])

67

In [14]:
len(train_outputs)

2001

In [15]:
dev_first_half = pd.DataFrame({})
for i in range(len(dev_outputs)):
    dev_first_half.insert(i, i, dev_outputs[i][2][0][0][(tokenized_dev_data["target_idx"][i]
        + tokenized_dev_data["target_length"][i]
        - 1)], True)

In [16]:
train_first_half = pd.DataFrame({})
for i in range(len(train_outputs)):
    train_first_half.insert(i, i, train_outputs[i][2][0][0][(tokenized_train_data["target_idx"][i]
        + tokenized_train_data["target_length"][i]
        - 1)], True)

In [17]:
type(dev_first_half.iloc[0,0])

numpy.float32

In [18]:
(train_first_half)

0         1         2         3         4         5         6     \
0   -0.160397 -0.465946  0.046189  0.157142  0.119402 -0.322285 -0.598058   
1   -0.247477  0.178935 -0.489686  0.373937  0.724113  0.482926  0.422667   
2    0.609990  0.443880  0.074903 -0.796771 -1.504554  0.567761  1.182435   
3    1.746693 -1.162306 -0.250420  1.568535  1.322894  0.888936  0.441441   
4   -0.051755 -0.454033  0.379584 -0.640485 -1.018485 -0.221455  0.132642   
..        ...       ...       ...       ...       ...       ...       ...   
763 -0.167999  0.345395  1.222324 -0.378696 -0.423635  0.396714 -1.204175   
764  0.129735  0.487435 -0.371600  0.280213  0.511724 -1.204140 -0.616163   
765  0.235709 -1.182512  1.250421  0.091299 -0.555647  0.727295 -0.296666   
766 -0.994451 -0.778055 -0.536706 -1.360759 -1.105136 -1.209358  1.265844   
767 -0.654545  0.377528 -0.215551 -1.364692 -0.889677  0.652186 -0.471079   

         7         8         9     ...      1991      1992      1993  \
0    0.423031  0.705193 -0.530531  ...  0.119402  0.449336 -0.052459   
1    1.068439  0.986011 -0.341439  ...  0.724113  1.003065  0.339962   
2   -1.200396 -0.261499 -0.286571  ... -1.504554 -0.184161 -0.417382   
3    0.890069  0.947886  0.694506  ...  1.322894  1.035178  1.452963   
4   -0.867261 -0.516408 -1.084161  ... -1.018485 -0.661018  0.353570   
..        ...       ...       ...  ...       ...       ...       ...   
763 -0.384888 -0.131366 -0.053850  ... -0.423635 -0.108839 -0.364607   
764  0.655818  0.986339 -0.272427  ...  0.511724  1.054701  0.128550   
765 -0.546635 -0.199395 -0.548825  ... -0.555647 -0.054521  0.431769   
766 -1.187009 -1.158362  0.857644  ... -1.105136 -0.876026 -1.320177   
767 -0.284517 -0.623119 -0.950330  ... -0.889677 -0.681744 -0.908523   

         1994      1995      1996      1997      1998      1999      2000  
0    0.000717  0.487249  1.021262  0.244510 -0.697815 -0.032693  0.659242  
1    0.566686 -0.709931  0.140538  1.100188 -0.145628 -0.383532  0.175225  
2   -1.123512 -0.243934 -0.836430 -1.104043  0.507302  0.296206 -1.101637  
3    1.231790 -0.207604 -1.186854  0.845895  1.429519  1.594262 -0.385489  
4   -0.415783 -0.244682 -1.003072 -0.963447 -2.333114 -0.099971 -0.207190  
..        ...       ...       ...       ...       ...       ...       ...  
763  0.036235  0.139229 -0.361963 -0.337259 -0.166678 -0.092807 -0.050182  
764 -0.303298  0.375411 -0.522113  0.711628  1.091578 -0.025689  0.471795  
765  0.262086 -0.506259  0.063512 -0.529751  0.919580 -0.080373 -1.271090  
766 -0.657063 -0.435954 -0.486775 -1.383283 -0.334221 -1.481967 -0.639636  
767 -0.738196 -0.343138  0.793274 -0.376730 -1.460569 -0.564272  0.657365  

[768 rows x 2001 columns]

In [19]:
dev_x = torch.tensor(dev_first_half.values)
train_x = torch.tensor(train_first_half.values)

In [20]:
type(dev_x)

torch.Tensor

In [60]:
type(train_x)

torch.Tensor

In [155]:
#WRONG
#
#

first_half_outputs = outputs[0:204][2][0]
first_halves = outputs[0:204][2][0][0][(tokenized_data["target_idx"][0:204]
        + tokenized_data["target_length"][0:204]
        - 1)]
first_halves.size()
second_halves = outputs[0:204][2][0][0][(tokenized_data["target_idx"][0:204]
        + tokenized_data["target_length"][0:204]
        - 1)]
type(second_halves[0][1])

torch.Tensor

In [63]:
test_idxs

NameError: name 'test_idxs' is not defined

I decided to use only the first half.


It's because using both could make the sizes confusing,
or the training less understandable

In [68]:
labels = tokenized_dev_data["type"].unique()
type(labels)

numpy.ndarray

In [69]:
text_dev_y = tokenized_dev_data["type"]

print(labels)
print(type(text_dev_y))

text_dev_y

['Sing' 'Plur']
<class 'pandas.core.series.Series'>


0      Sing
1      Plur
2      Sing
3      Sing
4      Plur
       ... 
194    Sing
195    Sing
196    Plur
197    Plur
198    Plur
Name: type, Length: 199, dtype: object

In [70]:
text_train_y = tokenized_train_data["type"]

print(labels)
print(type(text_train_y))

text_train_y


['Sing' 'Plur']
<class 'pandas.core.series.Series'>


0       Sing
1       Sing
2       Sing
3       Plur
4       Sing
        ... 
1995    Plur
1996    Plur
1997    Plur
1998    Sing
1999    Sing
Name: type, Length: 2000, dtype: object

In [71]:
#transforming train_y to a series of number by the labels
dev_y=[]

for i in range(text_dev_y.size):
    dev_y.append(np.where(labels == text_dev_y[i])[0][0])
    
dev_y

[0,
 1,
 0,
 0,
 1,
 1,
 0,
 0,
 0,
 1,
 0,
 1,
 0,
 0,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 1,
 0,
 1,
 0,
 1,
 1,
 1,
 0,
 0,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 1,
 0,
 1,
 1,
 0,
 1,
 1,
 0,
 1,
 1,
 1,
 0,
 1,
 0,
 1,
 1,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 1,
 1,
 0,
 0,
 0,
 0,
 1,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 1,
 1,
 0,
 1,
 0,
 0,
 1,
 1,
 0,
 0,
 0,
 0,
 1,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 0,
 0,
 1,
 1,
 1,
 0,
 1,
 0,
 0,
 1,
 0,
 1,
 0,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 0,
 0,
 0,
 1,
 1,
 1,
 0,
 0,
 0,
 0,
 1,
 1,
 0,
 1,
 0,
 0,
 1,
 1,
 0,
 0,
 1,
 1,
 1,
 1,
 0,
 1,
 0,
 0,
 1,
 1,
 1,
 1,
 0,
 0,
 1,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 1,
 1]

In [72]:
dev_y=torch.tensor(dev_y)

In [73]:
train_y=[]

for i in range(text_train_y.size):
    train_y.append(np.where(labels == text_train_y[i])[0][0])
train_y

[0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 1,
 0,
 1,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 1,
 1,
 0,
 0,
 0,
 1,
 1,
 0,
 0,
 1,
 0,
 1,
 0,
 1,
 1,
 0,
 1,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 1,
 0,
 1,
 1,
 0,
 1,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 1,
 0,
 0,
 1,
 0,
 1,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 1,
 0,
 1,
 0,
 0,
 1,
 0,
 0,
 1,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 1,
 1,
 0,
 1,
 0,
 0,
 1,
 1,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 1,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 1,
 0,
 1,
 1,
 0,
 1,
 0,
 0,
 0,
 1,
 1,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 1,
 0,
 0,
 1,
 0,
 0,
 1,
 0,
 1,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 1,
 0,
 0,
 1,
 1,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 1,
 0,
 0,
 0,
 1,
 1,
 1,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 1,
 0,


In [74]:
train_y=torch.tensor(train_y)

In [75]:
print(type(dev_x[1]), type(dev_y))
print(type(train_x[1]), type(train_y))

<class 'torch.Tensor'> <class 'torch.Tensor'>
<class 'torch.Tensor'> <class 'torch.Tensor'>


In [76]:
dev_y

tensor([0, 1, 0, 0, 1, 1, 0, 0, 0, 1, 0, 1, 0, 0, 1, 1, 1, 0, 1, 1, 1, 0, 0, 1,
        0, 0, 0, 0, 1, 0, 0, 0, 0, 1, 1, 0, 1, 0, 1, 1, 1, 0, 0, 1, 1, 0, 1, 1,
        1, 1, 1, 1, 1, 1, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 1, 0, 1, 1, 0, 1, 1, 0,
        1, 1, 1, 0, 1, 0, 1, 1, 1, 0, 0, 0, 0, 0, 1, 1, 1, 0, 0, 0, 0, 1, 1, 0,
        1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 1, 1, 0, 1, 0, 0, 1, 1, 0, 0,
        0, 0, 1, 1, 1, 1, 0, 1, 1, 1, 0, 0, 1, 1, 1, 0, 1, 0, 0, 1, 0, 1, 0, 1,
        1, 1, 0, 1, 1, 1, 0, 0, 0, 1, 1, 1, 0, 0, 0, 0, 1, 1, 0, 1, 0, 0, 1, 1,
        0, 0, 1, 1, 1, 1, 0, 1, 0, 0, 1, 1, 1, 1, 0, 0, 1, 0, 1, 0, 1, 0, 0, 0,
        1, 0, 0, 0, 1, 1, 1])

In [77]:
train_y

tensor([0, 0, 0,  ..., 1, 0, 0])

In [78]:
dev_x.size()

torch.Size([768, 199])

In [79]:
dev_x = torch.transpose(dev_x, 0,1)

In [80]:
train_x = torch.transpose(train_x, 0,1)

In [81]:
print("train size:", train_x.size(), train_y.size())
print("train size:", dev_x.size(), dev_y.size())

train size: torch.Size([2000, 768]) torch.Size([2000])
train size: torch.Size([199, 768]) torch.Size([199])


Random indexes

In [82]:
dev_idx = np.arange(len(dev_y))
np.random.shuffle(dev_idx)
train_idx = np.arange(len(train_y))
np.random.shuffle(train_idx)

Batching Class

In [83]:
class BatchIterator:
    def __init__(self, x, y, batch_size):
        self.x = x
        self.y = y
        self.batch_size = batch_size
        
    def iterate_once(self):
        for start in range(0, len(self.x), self.batch_size):
            end = start + self.batch_size
            yield self.x[start:end], self.y[start:end]

Test the iterator:

In [84]:
train_iter = BatchIterator(torch.Tensor([1,2,3,4,5,6]), torch.Tensor([3,3,3,3,3]), 200)

for batch in train_iter.iterate_once():
    print(batch[0].size(), batch[1].size())

torch.Size([6]) torch.Size([5])


The classifier

First try

In [85]:
class Classifier(nn.Module):
    def __init__(self, input_dim, output_dim, hidden_dim):
        super().__init__()
        self.input_layer = nn.Linear(input_dim, hidden_dim)
        self.relu = nn.ReLU()
        self.output_layer = nn.Linear(hidden_dim, output_dim)
        
    def forward(self, X):
        h = self.input_layer(X)
        h = self.relu(h)
        out = self.output_layer(h)
        return out

Model Instance

In [86]:
model = Classifier(
    input_dim = train_x.size(1),
    output_dim = labels.size,
    hidden_dim = 50
)
model

Classifier(
  (input_layer): Linear(in_features=768, out_features=50, bias=True)
  (relu): ReLU()
  (output_layer): Linear(in_features=50, out_features=2, bias=True)
)

In [87]:
for n, p in model.named_parameters():
    print(n, p.size())

input_layer.weight torch.Size([50, 768])
input_layer.bias torch.Size([50])
output_layer.weight torch.Size([2, 50])
output_layer.bias torch.Size([2])


Loss function and optimizer

In [88]:
criterion = nn.CrossEntropyLoss()
optimizer = optim.Adam(model.parameters())

Testing out the performance

At this point it should be around random so around 10%

In [89]:
test_pred = model(dev_x).max(axis=1)[1]
test_acc = torch.eq(test_pred, dev_y).sum().float() / len(dev_x)


tensor(0.5729)

Training Loop

In [90]:
batch_size = 50
train_iter = BatchIterator(train_x, train_y, batch_size)
dev_iter = BatchIterator(dev_x, dev_y, batch_size)

all_train_loss = []
all_dev_loss = []
all_train_acc = []
all_dev_acc =[]

n_epochs = 10
for epoch in range(n_epochs):
    #training loop
    for bi, (batch_x, batch_y) in enumerate(train_iter.iterate_once()):
        

        y_out = model(batch_x)
        
        loss = criterion(y_out, batch_y)
        optimizer.zero_grad()
        loss.backward()    
        optimizer.step()
    
    train_out = model(train_x)
    train_loss = criterion(train_out, train_y)
    all_train_loss.append(train_loss.item())
    train_pred = train_out.max(axis=1)[1]
    train_acc = torch.eq(train_pred, train_y).sum().float() / len(train_x)
    all_train_acc.append(train_acc)
    
    dev_out = model(dev_x)
    dev_loss = criterion(dev_out, dev_y)
    all_dev_loss.append(dev_loss.item())
    dev_pred = dev_out.max(axis=1)[1]
    dev_acc = torch.eq(dev_pred, dev_y).sum().float() / len(dev_x)
    all_dev_acc.append(dev_acc)
    
    print(f"Epoch: {epoch}\n train_accuracy: {train_acc} train loss: {train_loss}")
    print(f"  dev accuracy: {dev_acc}  dev loss: {dev_loss}")

Epoch: 0
 train_accuracy: 0.9415000081062317 train loss: 0.15632030367851257
  dev accuracy: 0.9195979833602905  dev loss: 0.23106826841831207
Epoch: 1
 train_accuracy: 0.9440000057220459 train loss: 0.12488677352666855
  dev accuracy: 0.9246231317520142  dev loss: 0.21577401459217072
Epoch: 2
 train_accuracy: 0.9440000057220459 train loss: 0.11474515497684479
  dev accuracy: 0.9246231317520142  dev loss: 0.19886456429958344
Epoch: 3
 train_accuracy: 0.9484999775886536 train loss: 0.10866516083478928
  dev accuracy: 0.9246231317520142  dev loss: 0.19267988204956055
Epoch: 4
 train_accuracy: 0.9514999985694885 train loss: 0.10458867996931076
  dev accuracy: 0.929648220539093  dev loss: 0.18781733512878418
Epoch: 5
 train_accuracy: 0.9520000219345093 train loss: 0.10180651396512985
  dev accuracy: 0.9246231317520142  dev loss: 0.18728964030742645
Epoch: 6
 train_accuracy: 0.9539999961853027 train loss: 0.0976124033331871
  dev accuracy: 0.9246231317520142  dev loss: 0.18654637038707733
E